In [1]:
import wave
import librosa
import IPython.display as ipd

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# **Function to convert data into Binary list**

In [3]:
def get_binary(data):

        # list of binary codes
        # of given data
        newd = []

        for i in data:
            newd.append(format(ord(i), '08b'))
        return newd

# **Encoding Function**

In [10]:
def encode(cov_song,msg):
  frm_bytes=bytearray(list(cov_song.readframes(cov_song.getnframes())))
  list_data=get_binary(msg)
  if(len(frm_bytes)<(len(list_data)*9)):
    return 0

  j=0
  frms=[]
  for i in range (len(list_data)):
    arr=[]
    for k in range(j,j+9):
      arr.append(frm_bytes[k])
    j=j+9
    
    
    for s in range(0, 8):
      if (list_data[i][s] == '0' and arr[s]% 2 != 0):
        arr[s] -= 1
      elif (list_data[i][s] == '1' and arr[s] % 2 == 0):
        if(arr[s] != 0):
          arr[s] -= 1
        else:
          arr[s] += 1
    
    if (i == (len(list_data) - 1)):
      if (arr[-1] % 2 == 0):
        if(arr[-1] != 0):
          arr[-1] -= 1
        else:
          arr[-1] += 1
    else:
      if (arr[-1] % 2 != 0):
        arr[-1] -= 1
    
    for t in arr:
      frms.append(t)


  for i in range(len(frms),len(frm_bytes)):
    frms.append(frm_bytes[i])
  
  frm_final=bytes(frms)


  with wave.open("/content/drive/MyDrive/embedded.wav", 'wb') as fd:
    fd.setparams(cov_song.getparams())
    fd.writeframes(frm_final)
  
  return 1

# **Decoding Function**

In [5]:
def decode(embedded_song):
  frm_bytes=bytearray(list(embedded_song.readframes(embedded_song.getnframes())))
  bin=''
  data=''
  for i in range(0,len(frm_bytes)):
    if((i+1)%9==0 and (frm_bytes[i]%2)==1):
      break
    elif((i+1)%9==0):
      data += chr(int(bin, 2))
      bin=''
    else:
      if (frm_bytes[i]%2==0):
        bin += '0'
      else:
        bin += '1'
  data += chr(int(bin, 2))
  return data

# **User will input the secret message and call the encoding function**

In [6]:
enco=0
data=input("Enter secret messsage: ")
cov_song=wave.open("/content/drive/MyDrive/cover_audio.wav")
status=encode(cov_song,data)
if(status==0):
  print("Length of message is very large, It cannot be embeded into the audio file")
else:
  print("Message has been successfully embedded into the Audio")
enco=1

Enter secret messsage: This is the secret message we embed into the Audio file
Message has been successfully embedded into the Audio


# **If Encoding is processed then user can call the decode function to extract the secret message**

In [7]:
if(enco==1):
  embedded_song=wave.open("/content/drive/MyDrive/embedded.wav", mode='rb')
  ext_data=decode(embedded_song)
  print(ext_data)

This is the secret message we embed into the Audio file


# **Cover Song before message is embedded**

In [8]:
cov_Path='/content/drive/MyDrive/cover_audio.wav'
x, sr = librosa.load(cov_Path) 
ipd.Audio(x, rate=sr)

# **Song after message is embedded**

In [9]:
embedded_Path='/content/drive/MyDrive/embedded.wav'
x, sr = librosa.load(embedded_Path) 
ipd.Audio(x, rate=sr)